# NEM 5-Minute Spot-Price Nowcast Analysis 

**Australia's National Electricity Market Price Prediction**

This notebook provides a complete end-to-end analysis of electricity spot price predictions for three major regions:
- **QLD1** - Queensland 
- **NSW1** - New South Wales 
- **VIC1** - Victoria 

---

##  Project Overview

We build and evaluate machine learning models to predict the **next 5-minute Regional Reference Price (RRP)** using:
- **Lag features**: Recent prices and demand (1, 2, and 12 intervals back = 5min, 10min, 60min)
- **Calendar features**: Hour of day and day of week
- **Models**: Linear Regression (baseline) + XGBoost/RandomForest

**Data Period**: September - October 2025 (~6 weeks, last 7 days used for testing)

---

## 1. Import Required Libraries

In [1]:
# Core data manipulation
import pandas as pd
import numpy as np
from pathlib import Path
import json
import warnings
warnings.filterwarnings('ignore')

# Machine Learning
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

# Visualisation
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Try to import XGBoost
try:
    from xgboost import XGBRegressor
    XGBOOST_AVAILABLE = True
    print(" XGBoost available")
except:
    XGBOOST_AVAILABLE = False
    print(" XGBoost not available, using RandomForest")

# Configure plotting
plt.style.use('seaborn-v0_8-darkgrid')
sns.set_palette("husl")
pd.options.display.max_columns = 50

print(" All libraries imported successfully")

✓ XGBoost available
✓ All libraries imported successfully


## 2. Load and Explore Data

Load the CSV files from `data/raw/` directory and combine all regions.

In [10]:
# Load all CSV files
raw_path = Path('data/raw')
csv_files = list(raw_path.glob('*.csv'))

print(f"Found {len(csv_files)} CSV files:")
for f in csv_files:
    print(f"  - {f.name}")

# Read and combine all files
dfs = []
for csv_file in csv_files:
    df = pd.read_csv(csv_file)
    dfs.append(df)

# Combine all dataframes
data = pd.concat(dfs, ignore_index=True)

# Parse timestamp
data['SETTLEMENTDATE'] = pd.to_datetime(data['SETTLEMENTDATE'])

# Sort by time
data = data.sort_values('SETTLEMENTDATE').reset_index(drop=True)

# Remove duplicates
data = data.drop_duplicates(subset=['SETTLEMENTDATE', 'REGION'], keep='first')

print(f"\n Combined dataset shape: {data.shape}")
print(f" Date range: {data['SETTLEMENTDATE'].min()} to {data['SETTLEMENTDATE'].max()}")
print(f" Regions: {data['REGION'].unique().tolist()}")
print(f"\n Columns: {data.columns.tolist()}")

Found 6 CSV files:
  - NSW_September_2025.csv
  - Queensland_October_2025.csv
  - Victoria_September_2025.csv
  - Victoria_October_2025.csv
  - NSW_October_2025.csv
  - Queensland_September_2025.csv

✓ Combined dataset shape: (38016, 5)
✓ Date range: 2025-09-01 00:05:00 to 2025-10-15 00:00:00
✓ Regions: ['NSW1', 'VIC1', 'QLD1']

✓ Columns: ['REGION', 'SETTLEMENTDATE', 'TOTALDEMAND', 'RRP', 'PERIODTYPE']


In [11]:
# Display first few rows
data.head(10)

REGION      SETTLEMENTDATE  TOTALDEMAND     RRP PERIODTYPE
0   NSW1 2025-09-01 00:05:00      7780.94  120.06      TRADE
1   VIC1 2025-09-01 00:05:00      5116.22  103.95      TRADE
2   QLD1 2025-09-01 00:05:00      5669.89  107.83      TRADE
3   NSW1 2025-09-01 00:10:00      7800.48  138.35      TRADE
4   VIC1 2025-09-01 00:10:00      5106.87  119.83      TRADE
5   QLD1 2025-09-01 00:10:00      5681.13  122.71      TRADE
6   NSW1 2025-09-01 00:15:00      7684.73  123.48      TRADE
7   VIC1 2025-09-01 00:15:00      5118.90  107.91      TRADE
8   QLD1 2025-09-01 00:15:00      5664.70  108.75      TRADE
9   NSW1 2025-09-01 00:20:00      7671.49  122.49      TRADE

In [12]:
# Dataset info
print("Dataset Information:")
print(data.info())
print("\nBasic Statistics:")
data.describe()

Dataset Information:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 38016 entries, 0 to 38015
Data columns (total 5 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   REGION          38016 non-null  object        
 1   SETTLEMENTDATE  38016 non-null  datetime64[ns]
 2   TOTALDEMAND     38016 non-null  float64       
 3   RRP             38016 non-null  float64       
 4   PERIODTYPE      38016 non-null  object        
dtypes: datetime64[ns](1), float64(2), object(2)
memory usage: 1.5+ MB
None

Basic Statistics:


SETTLEMENTDATE   TOTALDEMAND           RRP
count                38016  38016.000000  38016.000000
mean   2025-09-23 00:02:30   5683.287832     55.301019
min    2025-09-01 00:05:00   1608.760000  -1000.000000
25%    2025-09-12 00:03:45   4529.940000    -10.010000
50%    2025-09-23 00:02:30   5551.235000     55.140000
75%    2025-10-04 00:01:15   6756.035000     95.670000
max    2025-10-15 00:00:00  10253.920000  20300.000000
std                    NaN   1481.965225    127.398914

## 3. Data Cleaning and Preprocessing

Filter to required columns and check for data quality issues.

In [13]:
# Keep only required columns
data = data[['SETTLEMENTDATE', 'REGION', 'RRP', 'TOTALDEMAND']].copy()

# Check for missing values
print("Missing values:")
print(data.isnull().sum())

# Check data types
print("\nData types:")
print(data.dtypes)

# Summary by region
print("\nData points per region:")
print(data['REGION'].value_counts())

Missing values:
SETTLEMENTDATE    0
REGION            0
RRP               0
TOTALDEMAND       0
dtype: int64

Data types:
SETTLEMENTDATE    datetime64[ns]
REGION                    object
RRP                      float64
TOTALDEMAND              float64
dtype: object

Data points per region:
REGION
NSW1    12672
VIC1    12672
QLD1    12672
Name: count, dtype: int64


## 4. Exploratory Data Analysis (EDA)

### 4.1 Price and Demand Distributions

## 3.5. Outlier Detection and Removal

Identify and remove extreme outliers that could distort our analysis and model training.

In [15]:
# Check for extreme outliers in RRP
print("Price statistics before outlier removal:")
print(data.groupby('REGION')['RRP'].describe())
print("\n" + "="*60)

# Visualize potential outliers
fig = px.box(data, x='REGION', y='RRP', color='REGION',
             title='RRP Distribution - Identifying Outliers',
             labels={'RRP': 'Price ($/MWh)', 'REGION': 'Region'},
             points='all')  # Show all points
fig.update_yaxes(range=[0, 1000])  # Focus on reasonable range
fig.show()

# Find extreme outliers (e.g., prices > $10,000/MWh)
outliers = data[data['RRP'] > 10000].copy()
print(f"\n Found {len(outliers)} extreme outlier(s) (RRP > $10,000/MWh):")
if len(outliers) > 0:
    print(outliers[['SETTLEMENTDATE', 'REGION', 'RRP', 'TOTALDEMAND']])
    
# Also check for the specific NSW outlier around October 10, 2025
nsw_oct = data[(data['REGION'] == 'NSW1') & 
               (data['SETTLEMENTDATE'].dt.date == pd.to_datetime('2025-10-10').date())]
extreme_nsw = nsw_oct[nsw_oct['RRP'] > 15000]
if len(extreme_nsw) > 0:
    print(f"\n  Specific NSW1 outlier on October 10, 2025:")
    print(extreme_nsw[['SETTLEMENTDATE', 'REGION', 'RRP', 'TOTALDEMAND']])

Price statistics before outlier removal:
          count       mean         std      min      25%    50%     75%  \
REGION                                                                    
NSW1    12672.0  68.803675  195.784838  -698.95  -6.9225  66.07  108.08   
QLD1    12672.0  50.923149   63.996915 -1000.00 -11.1000  59.83   85.73   
VIC1    12672.0  46.176234   77.342954   -81.71 -10.0000  19.00   90.00   

             max  
REGION            
NSW1    20300.00  
QLD1      528.73  
VIC1      623.92  




🔍 Found 1 extreme outlier(s) (RRP > $10,000/MWh):
           SETTLEMENTDATE REGION      RRP  TOTALDEMAND
34338 2025-10-10 17:55:00   NSW1  20300.0      8696.94

⚠️  Specific NSW1 outlier on October 10, 2025:
           SETTLEMENTDATE REGION      RRP  TOTALDEMAND
34338 2025-10-10 17:55:00   NSW1  20300.0      8696.94


In [16]:
# Remove extreme outliers (RRP > $10,000/MWh)
# These are likely data errors or market suspension events that would distort our nowcast model
data_before = len(data)
data = data[data['RRP'] <= 10000].copy()
data_after = len(data)
removed = data_before - data_after

print(f" Removed {removed} extreme outlier(s)")
print(f" Dataset size: {data_before} → {data_after} rows")
print("\n" + "="*60)
print("Price statistics after outlier removal:")
print(data.groupby('REGION')['RRP'].describe())

✓ Removed 1 extreme outlier(s)
✓ Dataset size: 38016 → 38015 rows

Price statistics after outlier removal:
          count       mean        std      min     25%    50%     75%      max
REGION                                                                        
NSW1    12671.0  67.207022  77.636454  -698.95  -6.925  66.06  108.08  1093.82
QLD1    12672.0  50.923149  63.996915 -1000.00 -11.100  59.83   85.73   528.73
VIC1    12672.0  46.176234  77.342954   -81.71 -10.000  19.00   90.00   623.92


In [7]:
# Price distribution by region
fig = px.box(data, x='REGION', y='RRP', color='REGION',
             title='RRP Distribution by Region',
             labels={'RRP': 'Price ($/MWh)', 'REGION': 'Region'})
fig.show()

In [8]:
# Demand distribution by region
fig = px.box(data, x='REGION', y='TOTALDEMAND', color='REGION',
             title='Total Demand Distribution by Region',
             labels={'TOTALDEMAND': 'Demand (MW)', 'REGION': 'Region'})
fig.show()

### 4.2 Time Series Exploration

In [9]:
# Price over time for all regions
fig = px.line(data, x='SETTLEMENTDATE', y='RRP', color='REGION',
              title='RRP Over Time - All Regions',
              labels={'SETTLEMENTDATE': 'Date', 'RRP': 'Price ($/MWh)'})
fig.update_xaxes(rangeslider_visible=True)
fig.show()

In [17]:
# Demand over time for all regions
fig = px.line(data, x='SETTLEMENTDATE', y='TOTALDEMAND', color='REGION',
              title='Demand Over Time - All Regions',
              labels={'SETTLEMENTDATE': 'Date', 'TOTALDEMAND': 'Demand (MW)'})
fig.update_xaxes(rangeslider_visible=True)
fig.show()

## 5. Feature Engineering

Create lag features and calendar features for each region.

In [19]:
def create_features(df_region):
    """Create lag and calendar features for a single region"""
    df = df_region.copy()
    
    # Sort by time
    df = df.sort_values('SETTLEMENTDATE').reset_index(drop=True)
    
    # Lag features (5 min, 10 min, 60 min ago)
    for lag in [1, 2, 12]:
        df[f'RRP_lag_{lag}'] = df['RRP'].shift(lag)
        df[f'TOTALDEMAND_lag_{lag}'] = df['TOTALDEMAND'].shift(lag)
    
    # Calendar features
    df['hour'] = df['SETTLEMENTDATE'].dt.hour
    df['weekday'] = df['SETTLEMENTDATE'].dt.weekday
    
    # Drop rows with NaN (from lag creation)
    df = df.dropna().reset_index(drop=True)
    
    return df

# Apply to each region
features_by_region = {}

for region in ['QLD1', 'NSW1', 'VIC1']:
    region_data = data[data['REGION'] == region].copy()
    features_df = create_features(region_data)
    features_by_region[region] = features_df
    print(f"{region}: {features_df.shape[0]} rows after feature engineering")
    
print("\n Feature engineering complete for all regions")

QLD1: 12660 rows after feature engineering
NSW1: 12659 rows after feature engineering
VIC1: 12660 rows after feature engineering

 Feature engineering complete for all regions


In [20]:
# Show feature columns for QLD1
print("Feature columns:")
print(features_by_region['QLD1'].columns.tolist())
print("\nFirst few rows with features:")
features_by_region['QLD1'].head()

Feature columns:
['SETTLEMENTDATE', 'REGION', 'RRP', 'TOTALDEMAND', 'RRP_lag_1', 'TOTALDEMAND_lag_1', 'RRP_lag_2', 'TOTALDEMAND_lag_2', 'RRP_lag_12', 'TOTALDEMAND_lag_12', 'hour', 'weekday']

First few rows with features:


SETTLEMENTDATE REGION     RRP  TOTALDEMAND  RRP_lag_1  \
0 2025-09-01 01:05:00   QLD1  108.75      5423.26     127.54   
1 2025-09-01 01:10:00   QLD1  123.76      5471.08     108.75   
2 2025-09-01 01:15:00   QLD1  107.83      5429.87     123.76   
3 2025-09-01 01:20:00   QLD1  107.83      5372.09     107.83   
4 2025-09-01 01:25:00   QLD1  100.49      5471.33     107.83   

   TOTALDEMAND_lag_1  RRP_lag_2  TOTALDEMAND_lag_2  RRP_lag_12  \
0            5510.46     108.75            5462.99      107.83   
1            5423.26     127.54            5510.46      122.71   
2            5471.08     108.75            5423.26      108.75   
3            5429.87     123.76            5471.08      107.83   
4            5372.09     107.83            5429.87      107.83   

   TOTALDEMAND_lag_12  hour  weekday  
0             5669.89     1        0  
1             5681.13     1        0  
2             5664.70     1        0  
3             5600.55     1        0  
4             5573.46     1        0

## 6. Train/Test Split (Temporal)

Split data: **last 7 days = test set**, everything before = training set.

In [21]:
def temporal_split(df, test_days=7):
    """Split data temporally - last N days for test"""
    max_date = df['SETTLEMENTDATE'].max()
    cutoff_date = max_date - pd.Timedelta(days=test_days)
    
    train = df[df['SETTLEMENTDATE'] < cutoff_date].copy()
    test = df[df['SETTLEMENTDATE'] >= cutoff_date].copy()
    
    return train, test

# Split each region
splits = {}

for region, df in features_by_region.items():
    train, test = temporal_split(df, test_days=7)
    splits[region] = {'train': train, 'test': test}
    print(f"{region}:")
    print(f"  Train: {len(train)} rows ({train['SETTLEMENTDATE'].min()} to {train['SETTLEMENTDATE'].max()})")
    print(f"  Test:  {len(test)} rows ({test['SETTLEMENTDATE'].min()} to {test['SETTLEMENTDATE'].max()})")
    print()

QLD1:
  Train: 10643 rows (2025-09-01 01:05:00 to 2025-10-07 23:55:00)
  Test:  2017 rows (2025-10-08 00:00:00 to 2025-10-15 00:00:00)

NSW1:
  Train: 10643 rows (2025-09-01 01:05:00 to 2025-10-07 23:55:00)
  Test:  2016 rows (2025-10-08 00:00:00 to 2025-10-15 00:00:00)

VIC1:
  Train: 10643 rows (2025-09-01 01:05:00 to 2025-10-07 23:55:00)
  Test:  2017 rows (2025-10-08 00:00:00 to 2025-10-15 00:00:00)



## 7. Model Training & Evaluation

Train two models for each region:
1. **Linear Regression** (baseline)
2. **XGBoost** or **RandomForest** (advanced model)

In [22]:
# Define feature columns (exclude timestamp and target)
feature_cols = ['RRP_lag_1', 'RRP_lag_2', 'RRP_lag_12',
                'TOTALDEMAND_lag_1', 'TOTALDEMAND_lag_2', 'TOTALDEMAND_lag_12',
                'hour', 'weekday', 'TOTALDEMAND']

# Train models for each region
results = {}

for region in ['QLD1', 'NSW1', 'VIC1']:
    print(f"\n{'='*60}")
    print(f"Training models for {region}")
    print('='*60)
    
    # Get train and test data
    train = splits[region]['train']
    test = splits[region]['test']
    
    X_train = train[feature_cols].values
    y_train = train['RRP'].values
    X_test = test[feature_cols].values
    y_test = test['RRP'].values
    
    # Train Linear Regression
    lr = LinearRegression()
    lr.fit(X_train, y_train)
    lr_pred = lr.predict(X_test)
    lr_mae = mean_absolute_error(y_test, lr_pred)
    print(f"\nLinear Regression MAE: ${lr_mae:.2f}/MWh")
    
    # Train XGBoost or RandomForest
    if XGBOOST_AVAILABLE:
        ml_model = XGBRegressor(random_state=42, n_jobs=-1, verbosity=0)
        ml_name = "XGBoost"
    else:
        ml_model = RandomForestRegressor(random_state=42, n_jobs=-1, n_estimators=100)
        ml_name = "RandomForest"
    
    ml_model.fit(X_train, y_train)
    ml_pred = ml_model.predict(X_test)
    ml_mae = mean_absolute_error(y_test, ml_pred)
    print(f"{ml_name} MAE: ${ml_mae:.2f}/MWh")
    
    # Select best model
    if lr_mae < ml_mae:
        best_model_name = "LinearRegression"
        best_pred = lr_pred
        best_mae = lr_mae
    else:
        best_model_name = ml_name
        best_pred = ml_pred
        best_mae = ml_mae
    
    print(f"\n Best model: {best_model_name} (MAE: ${best_mae:.2f}/MWh)")
    
    # Store results
    results[region] = {
        'train': train,
        'test': test,
        'y_test': y_test,
        'lr_pred': lr_pred,
        'ml_pred': ml_pred,
        'best_pred': best_pred,
        'lr_mae': lr_mae,
        'ml_mae': ml_mae,
        'best_model': best_model_name,
        'best_mae': best_mae
    }

print("\n" + "="*60)
print("TRAINING COMPLETE FOR ALL REGIONS")
print("="*60)


Training models for QLD1

Linear Regression MAE: $9.40/MWh
XGBoost MAE: $8.97/MWh

 Best model: XGBoost (MAE: $8.97/MWh)

Training models for NSW1

Linear Regression MAE: $18.71/MWh
XGBoost MAE: $17.91/MWh

 Best model: XGBoost (MAE: $17.91/MWh)

Training models for VIC1

Linear Regression MAE: $8.46/MWh
XGBoost MAE: $8.83/MWh

 Best model: LinearRegression (MAE: $8.46/MWh)

TRAINING COMPLETE FOR ALL REGIONS


## 8. Model Performance Summary

In [23]:
# Summary table
summary_data = []
for region, res in results.items():
    summary_data.append({
        'Region': region,
        'Linear Regression MAE ($)': f"{res['lr_mae']:.2f}",
        'ML Model MAE ($)': f"{res['ml_mae']:.2f}",
        'Best Model': res['best_model'],
        'Best MAE ($)': f"{res['best_mae']:.2f}",
        'Train Size': len(res['train']),
        'Test Size': len(res['test'])
    })

summary_df = pd.DataFrame(summary_data)
summary_df

Region Linear Regression MAE ($) ML Model MAE ($)        Best Model  \
0   QLD1                      9.40             8.97           XGBoost   
1   NSW1                     18.71            17.91           XGBoost   
2   VIC1                      8.46             8.83  LinearRegression   

  Best MAE ($)  Train Size  Test Size  
0         8.97       10643       2017  
1        17.91       10643       2016  
2         8.46       10643       2017

## 9. Interactive Visualisations

### 9.1 Time Series: Actual vs Predicted

In [24]:
# Create subplots for all three regions
fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=('Queensland (QLD1)', 'New South Wales (NSW1)', 'Victoria (VIC1)'),
    vertical_spacing=0.08,
    shared_xaxes=True
)

for i, region in enumerate(['QLD1', 'NSW1', 'VIC1'], 1):
    test_df = results[region]['test']
    y_test = results[region]['y_test']
    best_pred = results[region]['best_pred']
    
    # Actual prices
    fig.add_trace(
        go.Scatter(x=test_df['SETTLEMENTDATE'], y=y_test,
                   mode='lines', name=f'{region} Actual',
                   line=dict(width=2)),
        row=i, col=1
    )
    
    # Predicted prices
    fig.add_trace(
        go.Scatter(x=test_df['SETTLEMENTDATE'], y=best_pred,
                   mode='lines', name=f'{region} Predicted',
                   line=dict(dash='dash', width=2)),
        row=i, col=1
    )

fig.update_layout(
    height=900,
    title_text="Actual vs Predicted RRP - All Regions (Last 7 Days)",
    showlegend=True
)
fig.update_yaxes(title_text="Price ($/MWh)")
fig.update_xaxes(title_text="Date", row=3, col=1)
fig.show()

### 9.2 Scatter Plots: Prediction Accuracy

In [25]:
# Create scatter plot for all regions
scatter_data = []

for region in ['QLD1', 'NSW1', 'VIC1']:
    test_df = results[region]['test']
    y_test = results[region]['y_test']
    best_pred = results[region]['best_pred']
    
    for actual, pred in zip(y_test, best_pred):
        scatter_data.append({
            'Region': region,
            'Actual': actual,
            'Predicted': pred,
            'Error': abs(actual - pred)
        })

scatter_df = pd.DataFrame(scatter_data)

fig = px.scatter(scatter_df, x='Actual', y='Predicted', color='Region',
                 size='Error', hover_data=['Error'],
                 title='Prediction Accuracy: Actual vs Predicted RRP',
                 labels={'Actual': 'Actual Price ($/MWh)', 'Predicted': 'Predicted Price ($/MWh)'})

# Add perfect prediction line (y=x)
max_price = max(scatter_df['Actual'].max(), scatter_df['Predicted'].max())
fig.add_trace(go.Scatter(x=[0, max_price], y=[0, max_price],
                         mode='lines', name='Perfect Prediction',
                         line=dict(dash='dash', color='gray')))

fig.show()

### 9.3 Error Analysis by Hour of Day

In [26]:
# Calculate error by hour for each region
error_by_hour = []

for region in ['QLD1', 'NSW1', 'VIC1']:
    test_df = results[region]['test'].copy()
    test_df['error'] = abs(results[region]['y_test'] - results[region]['best_pred'])
    
    hourly_error = test_df.groupby('hour')['error'].mean().reset_index()
    hourly_error['Region'] = region
    error_by_hour.append(hourly_error)

error_by_hour_df = pd.concat(error_by_hour)

fig = px.bar(error_by_hour_df, x='hour', y='error', color='Region',
             barmode='group',
             title='Average Prediction Error by Hour of Day',
             labels={'hour': 'Hour of Day', 'error': 'Mean Absolute Error ($/MWh)'})
fig.show()

### 9.4 Error Distribution

In [27]:
# Error distribution histogram
fig = px.histogram(scatter_df, x='Error', color='Region', nbins=50,
                   title='Error Distribution by Region',
                   labels={'Error': 'Absolute Error ($/MWh)'},
                   marginal='box')
fig.show()

### 9.5 Regional Performance Comparison

In [28]:
# MAE comparison bar chart
mae_data = pd.DataFrame([
    {'Region': region, 'MAE': res['best_mae'], 'Model': res['best_model']}
    for region, res in results.items()
])

fig = px.bar(mae_data, x='Region', y='MAE', color='Model', text='MAE',
             title='Model Performance by Region (Mean Absolute Error)',
             labels={'MAE': 'MAE ($/MWh)'})
fig.update_traces(texttemplate='$%{text:.2f}', textposition='outside')
fig.show()

## 10. Export Results

Save predictions and metrics for each region.

In [29]:
# Create exports directory if it doesn't exist
export_path = Path('exports')
export_path.mkdir(exist_ok=True)

# Export predictions for each region
for region, res in results.items():
    test_df = res['test'].copy()
    
    # Create predictions dataframe
    pred_df = pd.DataFrame({
        'timestamp': test_df['SETTLEMENTDATE'].values,
        'actual': res['y_test'],
        'pred': res['best_pred'],
        'error': abs(res['y_test'] - res['best_pred']),
        'model': res['best_model'],
        'region': region
    })
    
    # Save to CSV
    csv_file = export_path / f'actual_vs_pred_{region}.csv'
    pred_df.to_csv(csv_file, index=False)
    print(f" Saved: {csv_file}")
    
    # Save metrics to JSON
    metrics = {
        'region': region,
        'best_model': res['best_model'],
        'mae': float(res['best_mae']),
        'n_train': len(res['train']),
        'n_test': len(res['test']),
        'feature_count': len(feature_cols)
    }
    
    json_file = export_path / f'metrics_{region}.json'
    with open(json_file, 'w') as f:
        json.dump(metrics, f, indent=2)
    print(f" Saved: {json_file}")
    print()

print(" All results exported successfully!")

 Saved: exports/actual_vs_pred_QLD1.csv
 Saved: exports/metrics_QLD1.json

 Saved: exports/actual_vs_pred_NSW1.csv
 Saved: exports/metrics_NSW1.json

 Saved: exports/actual_vs_pred_VIC1.csv
 Saved: exports/metrics_VIC1.json

 All results exported successfully!


##  Summary & Conclusions

### Key Findings:

1. **Victoria (VIC1)** shows the most predictable prices with lowest MAE
2. **New South Wales (NSW1)** has higher price volatility and prediction errors
3. **Queensland (QLD1)** performs well with stable predictions

### Model Performance:
- XGBoost generally outperforms Linear Regression for most regions
- Lag features (especially 1-interval lag) are strong predictors
- Calendar features capture daily patterns effectively

### Next Steps:
- Add weather data (temperature, solar, wind)
- Include interconnector flow features
- Incorporate generator outage schedules
- Extend prediction horizon (15-min, 30-min ahead)
- Try deep learning models (LSTM, Transformers)

---

**Project Complete! **

All results have been exported to the `exports/` directory and are ready for further analysis or sharing.